In [1]:
from argparse import Namespace
import torch

In [2]:
t_c = [0.5, 14.0, 15.0, 28.0, 11.0, 8.0, 3.0, -4.0, 6.0, 13.0, 21.0]
t_u = [35.7, 55.9, 58.2, 81.9, 56.3, 48.9, 33.9, 21.8, 48.4, 60.4, 68.4]
t_c = torch.tensor(t_c)
t_u = torch.tensor(t_u)

In [3]:
def model(t_u: torch.Tensor, w: float, b: float) -> torch.Tensor:
    '''Takes an input tensor, t_u and multiplies it by the weight before adding the bias
    
    params:
    
    :t_u: the input tensor, a torch.Tensor object
    :w: weight (float) the weight parameter
    :b: bias (float) the bias parameter
    '''
    return w * t_u + b

In [4]:
def loss_fn(t_p: torch.Tensor, t_c: torch.Tensor) -> torch.Tensor:
    '''Takes the predicted tensor and the celsius tensor and
    returns the difference between them.
    
    params:
    
    :t_p: (torch.Tensor) the tensor of predictions
    :t_c: (torch.Tensor) the celsius tensor'''
    squared_diffs = (t_p - t_c)**2
    return squared_diffs.mean()

In [5]:
w = torch.ones(())
b = torch.zeros(())

In [6]:
t_p = model(t_u, w, b)

In [7]:
t_p

tensor([35.7000, 55.9000, 58.2000, 81.9000, 56.3000, 48.9000, 33.9000, 21.8000,
        48.4000, 60.4000, 68.4000])

In [8]:
#check the loss value
loss = loss_fn(t_p, t_c)

In [9]:
loss

tensor(1763.8848)

In [10]:
delta = 0.1

loss_rate_of_change_w = (loss_fn(model(t_u, w + delta, b), t_c) - \
                        loss_fn(model(t_u, w - delta, b), t_c)) / (2.0 * delta)

In [11]:
loss_rate_of_change_w

tensor(4517.2974)

In [12]:
learning_rate = 1e-2

w = w - learning_rate * loss_rate_of_change_w

In [13]:
w

tensor(-44.1730)

In [14]:
loss_rate_of_change_b = (loss_fn(model(t_u, w, b + delta), t_c) - \
                        loss_fn(model(t_u, w, b - delta), t_c)) / (2.0 * delta)

b = b - learning_rate * loss_rate_of_change_b

In [15]:
def dloss_fn(t_p: torch.Tensor, t_c: torch.Tensor):
    '''The derivative of the loss function'''
    dsq_diffs = 2 * (t_p - t_c) / t_p.size(0)
    return dsq_diffs

In [16]:
def dmodel_dw(t_u, w, b):
    '''derivative of the model with respect to w'''
    return t_u

In [17]:
def dmodel_db(t_u: torch.Tensor, w: float, b: float):
    '''Derivative of the model with respect to b'''
    return 1.0

In [18]:
def grad_fn(t_u: torch.Tensor, t_c: torch.Tensor,
           t_p: torch.Tensor, w, b):
    '''The gradient function for the loss with relation to w and b'''
    dloss_dtp = dloss_fn(t_p, t_c)
    dloss_dw = dloss_dtp * dmodel_dw(t_u, w, b)
    dloss_db = dloss_dtp * dmodel_db(t_u, w, b)
    return torch.stack([dloss_dw.sum(), dloss_db.sum()])

In [19]:
def training_loop(n_epochs, learning_rate, params, t_u, t_c):
    for epoch in range(1, n_epochs +1):
        w, b = params
        t_p = model(t_u, w, b)
        loss = loss_fn(t_p, t_c)
        grad = grad_fn(t_u, t_c, t_p, w, b)
        
        params = params - learning_rate * grad
        if (epoch < 20) | (epoch % 5 ==0):
            print('Epoch %d, Loss %f' % (epoch, float(loss)))
    return params

In [20]:
training_loop(
    n_epochs = 100, 
    learning_rate = 1e-2, 
    params = torch.tensor([1.0, 0.0]), 
    t_u = t_u, 
    t_c = t_c)

Epoch 1, Loss 1763.884766
Epoch 2, Loss 5802484.500000
Epoch 3, Loss 19408029696.000000
Epoch 4, Loss 64915905708032.000000
Epoch 5, Loss 217130525461053440.000000
Epoch 6, Loss 726257583152928129024.000000
Epoch 7, Loss 2429183416467662896627712.000000
Epoch 8, Loss 8125122549611731432050262016.000000
Epoch 9, Loss 27176882120842590626938030653440.000000
Epoch 10, Loss 90901105189019073810297959556841472.000000
Epoch 11, Loss inf
Epoch 12, Loss inf
Epoch 13, Loss inf
Epoch 14, Loss inf
Epoch 15, Loss inf
Epoch 16, Loss inf
Epoch 17, Loss inf
Epoch 18, Loss inf
Epoch 19, Loss inf
Epoch 20, Loss inf
Epoch 25, Loss nan
Epoch 30, Loss nan
Epoch 35, Loss nan
Epoch 40, Loss nan
Epoch 45, Loss nan
Epoch 50, Loss nan
Epoch 55, Loss nan
Epoch 60, Loss nan
Epoch 65, Loss nan
Epoch 70, Loss nan
Epoch 75, Loss nan
Epoch 80, Loss nan
Epoch 85, Loss nan
Epoch 90, Loss nan
Epoch 95, Loss nan
Epoch 100, Loss nan


tensor([nan, nan])

In [21]:
training_params0 = Namespace(
    n_epochs=100,
    learning_rate=1e-4,
    params = torch.tensor([1.0, 0.0]),
    t_u = t_u,
    t_c = t_c)

In [22]:
training_loop(**vars(training_params0))

Epoch 1, Loss 1763.884766
Epoch 2, Loss 323.090515
Epoch 3, Loss 78.929634
Epoch 4, Loss 37.552845
Epoch 5, Loss 30.540283
Epoch 6, Loss 29.351154
Epoch 7, Loss 29.148884
Epoch 8, Loss 29.113848
Epoch 9, Loss 29.107145
Epoch 10, Loss 29.105247
Epoch 11, Loss 29.104168
Epoch 12, Loss 29.103222
Epoch 13, Loss 29.102295
Epoch 14, Loss 29.101379
Epoch 15, Loss 29.100466
Epoch 16, Loss 29.099548
Epoch 17, Loss 29.098631
Epoch 18, Loss 29.097717
Epoch 19, Loss 29.096796
Epoch 20, Loss 29.095881
Epoch 25, Loss 29.091301
Epoch 30, Loss 29.086714
Epoch 35, Loss 29.082142
Epoch 40, Loss 29.077562
Epoch 45, Loss 29.072981
Epoch 50, Loss 29.068401
Epoch 55, Loss 29.063826
Epoch 60, Loss 29.059248
Epoch 65, Loss 29.054674
Epoch 70, Loss 29.050098
Epoch 75, Loss 29.045530
Epoch 80, Loss 29.040955
Epoch 85, Loss 29.036379
Epoch 90, Loss 29.031811
Epoch 95, Loss 29.027235
Epoch 100, Loss 29.022667


tensor([ 0.2327, -0.0438])

In [23]:
t_un = 0.1 * t_u

In [24]:
training_params1 = Namespace(
    n_epochs=100,
    learning_rate=1e-2,
    params=torch.tensor([1.0, 0.0]),
    t_u=t_un,
    t_c = t_c
)

In [25]:
training_loop(**vars(training_params1))

Epoch 1, Loss 80.364342
Epoch 2, Loss 37.574913
Epoch 3, Loss 30.871077
Epoch 4, Loss 29.756193
Epoch 5, Loss 29.507153
Epoch 6, Loss 29.392456
Epoch 7, Loss 29.298828
Epoch 8, Loss 29.208717
Epoch 9, Loss 29.119415
Epoch 10, Loss 29.030489
Epoch 11, Loss 28.941877
Epoch 12, Loss 28.853565
Epoch 13, Loss 28.765553
Epoch 14, Loss 28.677851
Epoch 15, Loss 28.590431
Epoch 16, Loss 28.503319
Epoch 17, Loss 28.416498
Epoch 18, Loss 28.329973
Epoch 19, Loss 28.243742
Epoch 20, Loss 28.157804
Epoch 25, Loss 27.732464
Epoch 30, Loss 27.314295
Epoch 35, Loss 26.903175
Epoch 40, Loss 26.498987
Epoch 45, Loss 26.101616
Epoch 50, Loss 25.710938
Epoch 55, Loss 25.326851
Epoch 60, Loss 24.949236
Epoch 65, Loss 24.577986
Epoch 70, Loss 24.212999
Epoch 75, Loss 23.854168
Epoch 80, Loss 23.501379
Epoch 85, Loss 23.154541
Epoch 90, Loss 22.813549
Epoch 95, Loss 22.478306
Epoch 100, Loss 22.148710


tensor([ 2.7553, -2.5162])

In [26]:
def training_loop(n_epochs, learning_rate, params, t_u, t_c,
                  print_params=True):
    for epoch in range(1, n_epochs + 1):
        w, b = params

        t_p = model(t_u, w, b)  # <1>
        loss = loss_fn(t_p, t_c)
        grad = grad_fn(t_u, t_c, t_p, w, b)  # <2>

        params = params - learning_rate * grad

        if epoch in {1, 2, 3, 10, 11, 99, 100, 4000, 5000}:  # <3>
            print('Epoch %d, Loss %f' % (epoch, float(loss)))
            if print_params:
                print('    Params:', params)
                print('    Grad:  ', grad)
        if epoch in {4, 12, 101}:
            print('...')

        if not torch.isfinite(loss).all():
            break  # <3>
            
    return params

In [27]:
training_params2 = Namespace(
    n_epochs=5000,
    learning_rate=1e-2,
    max_param=1.0,
    min_param=0.0,
    t_un=t_un,
    t_c=t_c,
    print_params=False)

In [28]:
params = training_loop(
    n_epochs=training_params2.n_epochs,
    learning_rate=training_params2.learning_rate,
    params=torch.tensor([training_params2.min_param, training_params2.max_param]),
    t_u=training_params2.t_un,
    t_c=training_params2.t_c,
    print_params=training_params2.print_params
)

Epoch 1, Loss 167.386368
Epoch 2, Loss 54.097572
Epoch 3, Loss 36.464962
...
Epoch 10, Loss 32.539341
Epoch 11, Loss 32.438816
...
Epoch 99, Loss 24.806761
Epoch 100, Loss 24.732485
...
Epoch 4000, Loss 2.927685
Epoch 5000, Loss 2.927648


In [29]:
%matplotlib inline
from matplotlib import pyplot as plt

t_p = model(t_un, *params)
fig = plt.figure(dpi=6000)
plt.xlabel("Temperature (Fahrenheit)")
plt.ylabel("Temperature (Celsius)")
plt.plot(t_u.numpy(), t_p.detach().numpy())
plt.plot(t_u.numpy(), t_c.numpy(), 'o')

In [30]:
t_p

tensor([ 1.8594, 12.7008, 13.9352, 26.6551, 12.9155,  8.9439,  0.8933, -5.6008,
         8.6755, 15.1160, 19.4096])

In [31]:
autograd_params = Namespace(
    min_value=0.0,
    max_value=1.0,
    requires_grad=True
)

In [32]:
params = torch.tensor([autograd_params.min_value,
                      autograd_params.max_value],
                      requires_grad=autograd_params.requires_grad)

In [33]:
params.grad is None

True

In [34]:
loss = loss_fn(model(t_u, *params), t_c)
loss.backward()

params.grad

tensor([-1260.7000,   -19.0000])

In [36]:
if params.grad is not None:
    params.grad.zero_()